In [2]:
import os
# save using vs code
SCALA_VERSION = '2.12'
SPARK_VERSION = '3.1.3'
# Download Kafka Jar file, this for readStream.format("kafka"), "kafka" is a driver
# kafka driver code is part of Maven Jar file
# https://mvnrepository.com/artifact/org.apache.spark/spark-sql-kafka-0-10_2.12/3.1.3
# pyspark-shell shall download the jar file behind..
os.environ['PYSPARK_SUBMIT_ARGS'] = f'--packages org.apache.spark:spark-sql-kafka-0-10_{SCALA_VERSION}:{SPARK_VERSION} pyspark-shell'


In [3]:
# here we implement windowed candle data for 1 minute
# here we implement windowed candle data for 3 minute
# here we implement windowed candle data for 5 minute

#     kafka-topics  --create --bootstrap-server localhost:9092 --replication-factor 1 --partitions 1 --topic candles-1min 
#     kafka-console-consumer --bootstrap-server localhost:9092 --topic  candles-1min  --from-beginning
 
#     kafka-topics  --create --bootstrap-server localhost:9092 --replication-factor 1 --partitions 1 --topic candles-3min 
#     kafka-console-consumer --bootstrap-server localhost:9092 --topic  candles-3min  --from-beginning

#     kafka-topics  --create --bootstrap-server localhost:9092 --replication-factor 1 --partitions 1 --topic candles-5min 
#     kafka-console-consumer --bootstrap-server localhost:9092 --topic  candles-5min  --from-beginning


In [4]:
import findspark
findspark.init()

In [5]:
import pyspark


from pyspark.sql import SparkSession
# spark groupBy has default setting for spark.sql.shuffle.partitions as 200
# we set to  4, should NOT be done in production 
spark = SparkSession.builder.master("local[1]")\
                            .config('spark.sql.shuffle.partitions', 4)\
                            .appName("SparkStreamingKafkaCandles").getOrCreate()

22/05/25 01:45:11 WARN Utils: Your hostname, ubuntu-virtual-machine resolves to a loopback address: 127.0.1.1; using 192.168.174.129 instead (on interface ens33)
22/05/25 01:45:11 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address


:: loading settings :: url = jar:file:/opt/spark-3.1.3-bin-hadoop2.7/jars/ivy-2.4.0.jar!/org/apache/ivy/core/settings/ivysettings.xml


Ivy Default Cache set to: /home/ubuntu/.ivy2/cache
The jars for the packages stored in: /home/ubuntu/.ivy2/jars
org.apache.spark#spark-sql-kafka-0-10_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-4d8f8a43-941f-43ef-b6c5-879491f48116;1.0
	confs: [default]
	found org.apache.spark#spark-sql-kafka-0-10_2.12;3.1.3 in central
	found org.apache.spark#spark-token-provider-kafka-0-10_2.12;3.1.3 in central
	found org.apache.kafka#kafka-clients;2.6.0 in central
	found com.github.luben#zstd-jni;1.4.8-1 in central
	found org.lz4#lz4-java;1.7.1 in central
	found org.xerial.snappy#snappy-java;1.1.8.2 in central
	found org.slf4j#slf4j-api;1.7.30 in central
	found org.spark-project.spark#unused;1.0.0 in central
	found org.apache.commons#commons-pool2;2.6.2 in central
:: resolution report :: resolve 2237ms :: artifacts dl 13ms
	:: modules in use:
	com.github.luben#zstd-jni;1.4.8-1 from central in [default]
	org.apache.commons#commons-pool2;2.6.2 from centra

In [6]:
# read from kafka, here spark is consumer for kafka topic called test
# spark streaming works as dataframe/sql
# group.id is consumer group id
# subcribe is kafka topic
# "kafka" driver is not available by default with spark, we need to download it, we did on cell 1

kafkaDf = spark.readStream.format("kafka")\
  .option("kafka.bootstrap.servers", "localhost:9092")\
  .option("subscribe", "stock-ticks")\
  .option("group.id", "stock-ticks-group")\
  .load()

In [7]:
# key and value are binary type, we need to CAST To STRING type
kafkaDf.printSchema()
# timestampType values
# CreateTime:  Timestamp relates to message creation time as set by a Kafka client/producer
# LogAppendTime : Timestamp relates to the time a message was appended to a Kafka log.
# UnknownType

root
 |-- key: binary (nullable = true)
 |-- value: binary (nullable = true)
 |-- topic: string (nullable = true)
 |-- partition: integer (nullable = true)
 |-- offset: long (nullable = true)
 |-- timestamp: timestamp (nullable = true)
 |-- timestampType: integer (nullable = true)



In [8]:

# Kafka value, key are in binary format
# we need to type cast to STRING, 
# we pick only value, timestamp as we need for 10 minute window
ticksDf = kafkaDf.selectExpr("CAST(value AS STRING)", "timestamp")
ticksDf.printSchema() # we get only value as string

root
 |-- value: string (nullable = true)
 |-- timestamp: timestamp (nullable = true)



In [9]:
# echoOnconsole = ticksDf\
#                 .writeStream\
#                 .outputMode("update")\
#                 .format("console")\
#                 .option("truncate", False)\
#                 .start() # start the query. spark will subscribe for data

In [10]:
import pyspark.sql.functions as F
from pyspark.sql.types import StructField, StructType, DoubleType, StringType, LongType, TimestampType

schema = StructType( [
    StructField("symbol", StringType(), True),
    StructField("price", DoubleType(), True),
    StructField("volume", LongType(), True),
    StructField("timestamp", LongType(),  True)
])

In [11]:
# we parse value which is JSON string to kafka struct, 
# this create a new column [replacing existing value which is string] with type
jsonDf = ticksDf.withColumn("value", F.from_json("value", schema))
jsonDf.printSchema()

root
 |-- value: struct (nullable = true)
 |    |-- symbol: string (nullable = true)
 |    |-- price: double (nullable = true)
 |    |-- volume: long (nullable = true)
 |    |-- timestamp: long (nullable = true)
 |-- timestamp: timestamp (nullable = true)



In [12]:
# now extract all the sub fields symbol, price, volume, timestamp into data frame
# exisitng value, timestamp shall be removed. existing timestamp is value produced time, not a stock tick time
# value.timestamp that comes from producer is basically a event time
stockTickDf = jsonDf.select (F.col("value.*")) # extract all sub fields as schema
stockTickDf.printSchema()

root
 |-- symbol: string (nullable = true)
 |-- price: double (nullable = true)
 |-- volume: long (nullable = true)
 |-- timestamp: long (nullable = true)



In [13]:
stockTickDf = stockTickDf.withColumn("traded_value", F.col("price") * F.col("volume"))
stockTickDf.printSchema()

root
 |-- symbol: string (nullable = true)
 |-- price: double (nullable = true)
 |-- volume: long (nullable = true)
 |-- timestamp: long (nullable = true)
 |-- traded_value: double (nullable = true)



In [14]:
# we have data coming in stream, each record has timestamp
# we have milli seconds 1647283268253, the actual seconds Mon Mar 14 2022 14:41:08
# now we have to calculate 1 minute window, sum(volume) up to 1 minute
# after conversions, we take timestamp which is truncatd to minute instead of milli seconds, drop temp columns
stockTickDf = stockTickDf\
                .withColumn("timestampTemp", (F.col("timestamp") / 1000).cast("timestamp"))\
                .withColumn("trade_time", F.date_trunc("minute", F.col("timestampTemp")))\
                .drop("timestamp")\
                .drop("timestampTemp")\
                .withColumnRenamed("trade_time", "timestamp")
               

# echoOnconsole = stockTickDf\
#                 .writeStream\
#                 .outputMode("update")\
#                 .format("console")\
#                 .option("truncate", False)\
#                 .start() # start the query. spark will subscribe for data

In [15]:
# aggregate
# sum (volume), sum(traded_value), candles open, high, low, close [OHLC]
# groupBy by symbol, timestamp

# now add delayed record processing with waterMark
stockTickDf1Min = stockTickDf\
                            .withWatermark("timestamp", "1 seconds")\
                            .groupBy("symbol", F.window("timestamp", "60 seconds"))\
                          .agg( F.sum("volume").alias("volume"),\
                                F.sum("traded_value").alias("traded_value"),\
                                F.max("price").alias("high"),\
                                F.min("price").alias("low"),\
                                F.first("price").alias("first"),\
                                F.last("price").alias("last")\
                              )
stockTickDf1Min.printSchema()
echoOnconsole = stockTickDf1Min\
                .writeStream\
                .outputMode("update")\
                .format("console")\
                .option("truncate", False)\
                .start() # start the query. spark will subscribe for data

# write result to kafka
# we need to publish all the field together as value
# we take all columns, convert to json string
# publish json as value to kafka

stockTickDf1MinKafka = stockTickDf1Min\
                            .selectExpr("to_json(struct(*)) AS value")

stockTickDf1MinKafka\
            .writeStream\
             .format("kafka")\
            .outputMode("update")\
             .option("kafka.bootstrap.servers", "localhost:9092")\
            .option("topic", "candles-1min")\
            .option("checkpointLocation", "file:///tmp/spark3")\
            .start()
            
# use kafka console consumer to subscrbe candles-1min, command is given in 2 nd cell

root
 |-- symbol: string (nullable = true)
 |-- window: struct (nullable = false)
 |    |-- start: timestamp (nullable = true)
 |    |-- end: timestamp (nullable = true)
 |-- volume: long (nullable = true)
 |-- traded_value: double (nullable = true)
 |-- high: double (nullable = true)
 |-- low: double (nullable = true)
 |-- first: double (nullable = true)
 |-- last: double (nullable = true)



22/05/25 02:03:32 WARN StreamingQueryManager: Temporary checkpoint location created which is deleted normally when the query didn't fail: /tmp/temporary-4b407887-29b0-4274-aaee-2f45ed68a715. If it's required to delete it under any circumstances, please set spark.sql.streaming.forceDeleteTempCheckpointLocation to true. Important to know deleting temp checkpoint folder is best effort.


-------------------------------------------
Batch: 0
-------------------------------------------


+------+------+------+------------+----+---+-----+----+
|symbol|window|volume|traded_value|high|low|first|last|
+------+------+------+------------+----+---+-----+----+
+------+------+------+------------+----+---+-----+----+



22/05/25 02:04:14 WARN NetworkClient: [Producer clientId=producer-1] Error while fetching metadata with correlation id 1 : {candles-1min=LEADER_NOT_AVAILABLE}
22/05/25 02:04:14 WARN NetworkClient: [Producer clientId=producer-1] Error while fetching metadata with correlation id 3 : {candles-1min=LEADER_NOT_AVAILABLE}


...

-------------------------------------------
Batch: 7480
-------------------------------------------
+------+------------------------------------------+------+------------+----+---+-----+----+
|symbol|window                                    |volume|traded_value|high|low|first|last|
+------+------------------------------------------+------+------------+----+---+-----+----+
|RELAXO|{2022-05-25 19:53:00, 2022-05-25 19:54:00}|90    |1820.0      |30.0|8.0|8.0  |30.0|
+------+------------------------------------------+------+------------+----+---+-----+----+



-------------------------------------------
Batch: 7481
-------------------------------------------
+------+------------------------------------------+------+------------+----+----+-----+----+
|symbol|window                                    |volume|traded_value|high|low |first|last|
+------+------------------------------------------+------+------------+----+----+-----+----+
|TSLA  |{2022-05-25 19:54:00, 2022-05-25 19:55:00}|120   |1920.0      |16.0|16.0|16.0 |16.0|
+------+------------------------------------------+------+------------+----+----+-----+----+



-------------------------------------------
Batch: 7482
-------------------------------------------
+------+------+------+------------+----+---+-----+----+
|symbol|window|volume|traded_value|high|low|first|last|
+------+------+------+------------+----+---+-----+----+
+------+------+------+------------+----+---+-----+----+



-------------------------------------------
Batch: 7483
-------------------------------------------
+------+------------------------------------------+------+------------+----+---+-----+----+
|symbol|window                                    |volume|traded_value|high|low|first|last|
+------+------------------------------------------+------+------------+----+---+-----+----+
|TSLA  |{2022-05-25 19:54:00, 2022-05-25 19:55:00}|170   |2270.0      |16.0|7.0|16.0 |7.0 |
+------+------------------------------------------+------+------------+----+---+-----+----+



-------------------------------------------
Batch: 7484
-------------------------------------------
+------+------------------------------------------+------+------------+----+----+-----+----+
|symbol|window                                    |volume|traded_value|high|low |first|last|
+------+------------------------------------------+------+------------+----+----+-----+----+
|RELAXO|{2022-05-25 19:54:00, 2022-05-25 19:55:00}|120   |1440.0      |12.0|12.0|12.0 |12.0|
+------+------------------------------------------+------+------------+----+----+-----+----+

